# Use me to align datasets with embeddings

In [ ]:
import pandas as pd
import os
import numpy as np
import torch
from transformers import pipeline, AutoTokenizer
from datasets import Dataset
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import cosine_similarity
from scipy.optimize import linear_sum_assignment

/export/usuarios_ml4ds/ammesa/TFG-LLMs/.venv_ds/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
folder_path = '/export/usuarios_ml4ds/ammesa/Data/1_segmented_data/micro_unaligned'
file_name = 'wiki_unaligned_75_micro.parquet'
full_path = os.path.join(folder_path, file_name)

ds = pd.read_parquet(full_path)

In [4]:
ds

title  \
0                              George Washington   
1    1788–89 United States presidential election   
2    1788–89 United States presidential election   
3       1792 United States presidential election   
4                              50 State quarters   
..                                           ...   
395                      Tratado de Adrianópolis   
396             Tratado de Constantinopla (1832)   
397                    Tratado de Küçük Kaynarca   
398                    Tratado de Londres (1827)   
399                                  Zarato ruso   

                                               summary  \
0    George Washington (February 22, 1732 [O.S. Feb...   
1    Presidential elections were held in the United...   
2    Presidential elections were held in the United...   
3    Presidential elections were held in the United...   
4    The 50 State quarters (authorized by Pub. L. 1...   
..                                                 ...   
395  El Tratado de Edirne o Adrianópolis (14 de sep...   
396  El Tratado de Constantinopla fue el resultado ...   
397  El Tratado de Küçük Kaynarca (también deletrea...   
398  El Tratado de Londres para la pacificación de ...   
399  El Zarato ruso (en ruso: Русское царство, roma...   

                                                  text lang  \
0    George Washington (February 22, 1732 [O.S. Feb...   en   
1    Presidential elections were held in the United...   en   
2    Presidential elections were held in the United...   en   
3    Presidential elections were held in the United...   en   
4    The 50 State quarters (authorized by Pub. L. 1...   en   
..                                                 ...  ...   
395  El Tratado de Edirne o Adrianópolis (14 de sep...   es   
396  El Tratado de Constantinopla fue el resultado ...   es   
397  El Tratado de Küçük Kaynarca (también deletrea...   es   
398  El Tratado de Londres para la pacificación de ...   es   
399  El Zarato ruso (en ruso: Русское царство, roma...   es   

                                                   url  equivalence  label  \
0      https://en.wikipedia.org/wiki/George_Washington            1    0.0   
1    https://en.wikipedia.org/wiki/1788%E2%80%9389_...            1    0.0   
2    https://en.wikipedia.org/wiki/1788%E2%80%9389_...            1    0.0   
3    https://en.wikipedia.org/wiki/1792_United_Stat...            1    0.0   
4      https://en.wikipedia.org/wiki/50_State_quarters            1    0.0   
..                                                 ...          ...    ...   
395  https://en.wikipedia.org/wiki/Treaty_of_Adrian...            0    0.0   
396  https://en.wikipedia.org/wiki/Treaty_of_Consta...            0    0.0   
397  https://en.wikipedia.org/wiki/Treaty_of_K%C3%B...            0    0.0   
398  https://en.wikipedia.org/wiki/Treaty_of_London...            0    0.0   
399    https://en.wikipedia.org/wiki/Tsardom_of_Russia            0    0.0   

        id id_preproc  
0        0       EN_0  
1        1       EN_1  
2        2       EN_2  
3        3       EN_3  
4        4       EN_4  
..     ...        ...  
395  18045   ES_18045  
396  18046   ES_18046  
397  18047   ES_18047  
398  18048   ES_18048  
399  18049   ES_18049  

[400 rows x 9 columns]

In [5]:
es = pd.read_parquet('/export/usuarios_ml4ds/ammesa/Data/1_segmented_data/micro_unaligned/es_2025-06-04_segmented_dataset.parquet.gzip')
en = pd.read_parquet('/export/usuarios_ml4ds/ammesa/Data/1_segmented_data/micro_unaligned/en_2025-06-04_segmented_dataset.parquet.gzip')

In [6]:
es


title                                            summary  \
12657  George Washington  George Washington (Westmoreland, Virginia, Amé...   
12658  George Washington  George Washington (Westmoreland, Virginia, Amé...   
12659  George Washington  George Washington (Westmoreland, Virginia, Amé...   
12660  George Washington  George Washington (Westmoreland, Virginia, Amé...   
12661  George Washington  George Washington (Westmoreland, Virginia, Amé...   
...                  ...                                                ...   
17720        Zarato ruso  El Zarato ruso (en ruso: Русское царство, roma...   
17721        Zarato ruso  El Zarato ruso (en ruso: Русское царство, roma...   
17722        Zarato ruso  El Zarato ruso (en ruso: Русское царство, roma...   
17723        Zarato ruso  El Zarato ruso (en ruso: Русское царство, roma...   
17724        Zarato ruso  El Zarato ruso (en ruso: Русское царство, roma...   

                                                    text lang  \
12657  George Washington (Westmoreland, Virginia, Amé...   es   
12658  Washington empezó a ganar condecoraciones arma...   es   
12659  El Congreso Continental designó a Washington c...   es   
12660  En 1787, presidió la Convención de Filadelfia ...   es   
12661  Antes de la finalización de su período de gobi...   es   
...                                                  ...  ...   
17720  Posteriormente, Rusia entró en un periodo de c...   es   
17721  La Época de los Problemas incluyó una guerra c...   es   
17722  En 1609, Polonia intervino oficialmente en los...   es   
17723  Sobre Rusia durante el reinado de Alekséi Mijá...   es   
17724  Domostroy es un conjunto de reglamentos del si...   es   

                                                   url     id  equivalence  \
12657  https://en.wikipedia.org/wiki/George_Washington  12657            1   
12658  https://en.wikipedia.org/wiki/George_Washington  12658            1   
12659  https://en.wikipedia.org/wiki/George_Washington  12659            1   
12660  https://en.wikipedia.org/wiki/George_Washington  12660            1   
12661  https://en.wikipedia.org/wiki/George_Washington  12661            1   
...                                                ...    ...          ...   
17720  https://en.wikipedia.org/wiki/Tsardom_of_Russia  17720            0   
17721  https://en.wikipedia.org/wiki/Tsardom_of_Russia  17721            0   
17722  https://en.wikipedia.org/wiki/Tsardom_of_Russia  17722            0   
17723  https://en.wikipedia.org/wiki/Tsardom_of_Russia  17723            0   
17724  https://en.wikipedia.org/wiki/Tsardom_of_Russia  17724            0   

        id_preproc  
12657   ES_10000_0  
12658   ES_10000_1  
12659   ES_10000_2  
12660   ES_10000_3  
12661   ES_10000_4  
...            ...  
17720  ES_18049_15  
17721  ES_18049_16  
17722  ES_18049_17  
17723  ES_18049_18  
17724  ES_18049_19  

[5068 rows x 8 columns]

In [7]:
en

title                                            summary  \
0      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
12652              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12653              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12654              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12655              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12656              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
0      George Washington (February 22, 1732 [O.S. Feb...   en   
1      Born in the Colony of Virginia, Washington bec...   en   
2      Washington was unanimously elected the first U...   en   
3      Washington's image is an icon of American cult...   en   
4      George Washington was born on February 22, 173...   en   
...                                                  ...  ...   
12652  Boxty dough can also be boiled like dumplings....   en   
12653  Modern variations can include currants and rai...   en   
12654  The traditional preparation known from an 1854...   en   
12655  In Ireland, St. Brigid is the patron saint of ...   en   
12656  Likely Irish, possibly from the Irish arán boc...   en   

                                                   url     id  equivalence  \
0      https://en.wikipedia.org/wiki/George_Washington      0            1   
1      https://en.wikipedia.org/wiki/George_Washington      1            1   
2      https://en.wikipedia.org/wiki/George_Washington      2            1   
3      https://en.wikipedia.org/wiki/George_Washington      3            1   
4      https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                ...    ...          ...   
12652              https://en.wikipedia.org/wiki/Boxty  12652            0   
12653              https://en.wikipedia.org/wiki/Boxty  12653            0   
12654              https://en.wikipedia.org/wiki/Boxty  12654            0   
12655              https://en.wikipedia.org/wiki/Boxty  12655            0   
12656              https://en.wikipedia.org/wiki/Boxty  12656            0   

       id_preproc  
0          EN_0_0  
1          EN_0_1  
2          EN_0_2  
3          EN_0_3  
4          EN_0_4  
...           ...  
12652   EN_6049_6  
12653   EN_6049_7  
12654   EN_6049_8  
12655   EN_6049_9  
12656  EN_6049_10  

[12657 rows x 8 columns]

In [4]:
es = ds[ds['lang']=='es']
en = ds[ds['lang']=='en']

In [ ]:
model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')

en_embeddings_tensor = model.encode(en['text'].tolist(), convert_to_tensor=True).cpu()
es_embeddings_tensor = model.encode(es['text'].tolist(), convert_to_tensor=True).cpu()

en['embedding'] = [emb for emb in en_embeddings_tensor]
es['embedding'] = [emb for emb in es_embeddings_tensor]

en_embeddings = torch.stack(en['embedding'].tolist()).cpu().numpy()
es_embeddings = torch.stack(es['embedding'].tolist()).cpu().numpy()
similarity_matrix = cosine_similarity(en_embeddings, es_embeddings)

cost_matrix = 1 - similarity_matrix

row_ind, col_ind = linear_sum_assignment(cost_matrix)
# Only take the number of rows equal to the smaller dataset
min_len = min(len(en), len(es))
#usa esto para mantener el resto de columnas a traducir!!!
matched_en = en.iloc[row_ind[:min_len]].copy()
matched_es = es.iloc[col_ind[:min_len]].copy()

# Add matching IDs
matched_en['matched_id_preproc_es'] = matched_es['id_preproc'].values
matched_es['matched_id_preproc_en'] = matched_en['id_preproc'].values

matched_en.drop(columns=['embedding'], inplace=True)
matched_es.drop(columns=['embedding'], inplace=True)


In [9]:
matched_en

title  \
0           George Washington   
1           George Washington   
2           George Washington   
3           George Washington   
4           George Washington   
...                       ...   
12509  Bosnia and Herzegovina   
12511  Bosnia and Herzegovina   
12520  Bosnia and Herzegovina   
12522  Bosnia and Herzegovina   
12524  Bosnia and Herzegovina   

                                                 summary  \
0      George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington (February 22, 1732 [O.S. Feb...   
...                                                  ...   
12509  Bosnia and Herzegovina, sometimes known as Bos...   
12511  Bosnia and Herzegovina, sometimes known as Bos...   
12520  Bosnia and Herzegovina, sometimes known as Bos...   
12522  Bosnia and Herzegovina, sometimes known as Bos...   
12524  Bosnia and Herzegovina, sometimes known as Bos...   

                                                    text lang  \
0      George Washington (February 22, 1732 [O.S. Feb...   en   
1      Born in the Colony of Virginia, Washington bec...   en   
2      Washington was unanimously elected the first U...   en   
3      Washington's image is an icon of American cult...   en   
4      George Washington was born on February 22, 173...   en   
...                                                  ...  ...   
12509  Typical Bosnian songs are ganga, rera, and the...   en   
12511  Rural folk traditions in Bosnia and Herzegovin...   en   
12520  The Bosna Royal basketball club from Sarajevo ...   en   
12522  The Bosnian chess team was Champion of Yugosla...   en   
12524  Association football is the most popular sport...   en   

                                                     url     id  equivalence  \
0        https://en.wikipedia.org/wiki/George_Washington      0            1   
1        https://en.wikipedia.org/wiki/George_Washington      1            1   
2        https://en.wikipedia.org/wiki/George_Washington      2            1   
3        https://en.wikipedia.org/wiki/George_Washington      3            1   
4        https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                  ...    ...          ...   
12509  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12509            0   
12511  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12511            0   
12520  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12520            0   
12522  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12522            0   
12524  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12524            0   

        id_preproc matched_id_preproc_es  
0           EN_0_0            ES_10000_0  
1           EN_0_1            ES_10048_1  
2           EN_0_2           ES_10086_45  
3           EN_0_3           ES_10000_77  
4           EN_0_4            ES_10000_7  
...            ...                   ...  
12509  EN_6047_149          ES_18013_124  
12511  EN_6047_151           ES_18044_11  
12520  EN_6047_160          ES_18013_131  
12522  EN_6047_162          ES_18013_127  
12524  EN_6047_164          ES_18013_126  

[5068 rows x 9 columns]

In [10]:
matched_es['id_preproc'] = matched_es['id_preproc'].str.replace(r'^ES', 'T_EN', regex=True)


In [11]:
matched_es


title  \
12657     George Washington   
13996  Augustine Washington   
15067          Bill Clinton   
12734     George Washington   
12664     George Washington   
...                     ...   
16947             Eslovenia   
17637              Tragedia   
16954             Eslovenia   
16950             Eslovenia   
16949             Eslovenia   

                                                 summary  \
12657  George Washington (Westmoreland, Virginia, Amé...   
13996  Augustine Washington (Westmoreland, Virginia, ...   
15067  William Jefferson Clinton (nacido Blythe III;[...   
12734  George Washington (Westmoreland, Virginia, Amé...   
12664  George Washington (Westmoreland, Virginia, Amé...   
...                                                  ...   
16947  Eslovenia, cuyo nombre oficial es República de...   
17637  La tragedia es una forma literaria, teatral o ...   
16954  Eslovenia, cuyo nombre oficial es República de...   
16950  Eslovenia, cuyo nombre oficial es República de...   
16949  Eslovenia, cuyo nombre oficial es República de...   

                                                    text lang  \
12657  George Washington (Westmoreland, Virginia, Amé...   es   
13996  Agustín Washington nació en Westmoreland, Virg...   es   
15067  Algunos consideran que fue un presidente moder...   es   
12734  Junto con la familia biológica de Marta, como ...   es   
12664  George Washington nació el 22 de febrero de 17...   es   
...                                                  ...  ...   
16947  Entre los músicos populares contemporáneos est...   es   
17637  Estásimo: es la parte lírica-dramática donde e...   es   
16954  En balonmano, la selección masculina ha lograd...   es   
16950  El primer atleta esloveno en conseguir medalla...   es   
16949  Las disciplinas más populares en Eslovenia son...   es   

                                                     url     id  equivalence  \
12657    https://en.wikipedia.org/wiki/George_Washington  12657            1   
13996  https://en.wikipedia.org/wiki/Augustine_Washin...  13996            1   
15067         https://en.wikipedia.org/wiki/Bill_Clinton  15067            1   
12734    https://en.wikipedia.org/wiki/George_Washington  12734            1   
12664    https://en.wikipedia.org/wiki/George_Washington  12664            1   
...                                                  ...    ...          ...   
16947             https://en.wikipedia.org/wiki/Slovenia  16947            0   
17637              https://en.wikipedia.org/wiki/Tragedy  17637            0   
16954             https://en.wikipedia.org/wiki/Slovenia  16954            0   
16950             https://en.wikipedia.org/wiki/Slovenia  16950            0   
16949             https://en.wikipedia.org/wiki/Slovenia  16949            0   

           id_preproc matched_id_preproc_en  
12657    T_EN_10000_0                EN_0_0  
13996    T_EN_10048_1                EN_0_1  
15067   T_EN_10086_45                EN_0_2  
12734   T_EN_10000_77                EN_0_3  
12664    T_EN_10000_7                EN_0_4  
...               ...                   ...  
16947  T_EN_18013_124           EN_6047_149  
17637   T_EN_18044_11           EN_6047_151  
16954  T_EN_18013_131           EN_6047_160  
16950  T_EN_18013_127           EN_6047_162  
16949  T_EN_18013_126           EN_6047_164  

[5068 rows x 9 columns]

In [28]:
matched_ids = set(matched_en['id_preproc'])
rem = en[~en['id_preproc'].isin(matched_ids)].copy()
rem

title                                            summary  \
5      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
10     George Washington  George Washington (February 22, 1732 [O.S. Feb...   
12     George Washington  George Washington (February 22, 1732 [O.S. Feb...   
14     George Washington  George Washington (February 22, 1732 [O.S. Feb...   
16     George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
12652              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12653              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12654              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12655              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
12656              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
5      The family moved to a plantation on Little Hun...   en   
10     Washington's party reached the Ohio River in N...   en   
12     The rest of the Virginia Regiment joined Washi...   en   
14     The Virginia Regiment was reconstituted in Aug...   en   
16     Under Washington, the Virginia Regiment had de...   en   
...                                                  ...  ...   
12652  Boxty dough can also be boiled like dumplings....   en   
12653  Modern variations can include currants and rai...   en   
12654  The traditional preparation known from an 1854...   en   
12655  In Ireland, St. Brigid is the patron saint of ...   en   
12656  Likely Irish, possibly from the Irish arán boc...   en   

                                                   url     id  equivalence  \
5      https://en.wikipedia.org/wiki/George_Washington      5            1   
10     https://en.wikipedia.org/wiki/George_Washington     10            1   
12     https://en.wikipedia.org/wiki/George_Washington     12            1   
14     https://en.wikipedia.org/wiki/George_Washington     14            1   
16     https://en.wikipedia.org/wiki/George_Washington     16            1   
...                                                ...    ...          ...   
12652              https://en.wikipedia.org/wiki/Boxty  12652            0   
12653              https://en.wikipedia.org/wiki/Boxty  12653            0   
12654              https://en.wikipedia.org/wiki/Boxty  12654            0   
12655              https://en.wikipedia.org/wiki/Boxty  12655            0   
12656              https://en.wikipedia.org/wiki/Boxty  12656            0   

       id_preproc                                          embedding  
5          EN_0_5  [tensor(0.0786), tensor(0.4299), tensor(0.1437...  
10        EN_0_10  [tensor(0.1547), tensor(0.3479), tensor(-0.060...  
12        EN_0_12  [tensor(0.0951), tensor(0.1314), tensor(-0.002...  
14        EN_0_14  [tensor(-0.0306), tensor(0.3722), tensor(0.039...  
16        EN_0_16  [tensor(0.1008), tensor(0.3264), tensor(-0.169...  
...           ...                                                ...  
12652   EN_6049_6  [tensor(-0.0287), tensor(-0.2516), tensor(-0.0...  
12653   EN_6049_7  [tensor(-0.0999), tensor(-0.7661), tensor(0.36...  
12654   EN_6049_8  [tensor(-0.1616), tensor(-0.1326), tensor(0.00...  
12655   EN_6049_9  [tensor(0.1272), tensor(-0.0646), tensor(-0.07...  
12656  EN_6049_10  [tensor(0.0118), tensor(-0.0457), tensor(0.004...  

[7589 rows x 9 columns]

In [29]:
rem = rem.drop(columns=['embedding'])


In [44]:
def split(dataframe: pd.DataFrame, language: str):
    '''
    Takes an input dataset and splits its raw_text column into phrases separated by
    the dot (.)
    ----------------
    Parameters:
    dataframe: A Pandas dataframe that has been previously segmented into paragraphs. 
    '''
    def get_token_length(text):
        return len(tokenizer.encode(text, truncation=False))
    
    max_tokens  = int(512*0.9)
    #I append to lists not to pd.DataFrames
    data = []

    for i, row in dataframe.iterrows():
        
        split_text = row['text'].split(". ")

        filtered_text = filter(lambda x: x!='', split_text)

        phrases = list(filtered_text)

        #used to check max lengths
        tokenizer = AutoTokenizer.from_pretrained('Helsinki-NLP/opus-mt-en-es')

        for _, p in enumerate(phrases):

        #Handle sentences over token limit
            if get_token_length(p) < max_tokens:
                
                new_row = [
                row["title"], row["summary"], p, row["lang"], row["url"],
                None, #For the dynamic ID
                row["equivalence"], row["id_preproc"] + "_" + str(_)
                ]

                data.append(new_row)

                valid_entry = True      
    
                
        if language == 'en':

            en_df = pd.DataFrame(data, columns=["title", "summary", "text", "lang", "url", "index", "equivalence", "id_preproc"])
            en_df["index"] = range(len(en_df))
            split_en_df = en_df          



        else:
            raise(Exception(f'The language: {language} is not supported!'))

    return split_en_df

In [48]:
model = pipeline("translation", model='Helsinki-NLP/opus-mt-en-es', device=-1)

def translate_text(batch):
    translation_list = model(batch['text'])
    batch['translated_text'] = [text['translation_text'] for text in translation_list]
    return batch

/export/usuarios_ml4ds/ammesa/TFG-LLMs/.venv_ds/lib/python3.12/site-packages/transformers/models/marian/tokenization_marian.py:175: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")
Device set to use cpu


In [38]:
rem = split(rem, 'en')
rem = Dataset.from_pandas(rem)


In [41]:
copia = rem

In [42]:
copia.to_pandas()

title                                            summary  \
0      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
28179              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28180              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28181              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28182              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28183              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
0      The family moved to a plantation on Little Hun...   en   
1      When Augustine died in 1743, Washington inheri...   en   
2      Because of his father's death, Washington did ...   en   
3      He learned mathematics and land surveying, and...   en   
4      By early adulthood, he was writing with what h...   en   
...                                                  ...  ...   
28179  Brigid is the patron saint of dairy and she is...   en   
28180                                The tradition of St   en   
28181  Brigid may have roots in Ireland's pagan histo...   en   
28182  Boxty is served for St Brigid's Day with other...   en   
28183  Likely Irish, possibly from the Irish arán boc...   en   

                                                   url  index  equivalence  \
0      https://en.wikipedia.org/wiki/George_Washington      0            1   
1      https://en.wikipedia.org/wiki/George_Washington      1            1   
2      https://en.wikipedia.org/wiki/George_Washington      2            1   
3      https://en.wikipedia.org/wiki/George_Washington      3            1   
4      https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                ...    ...          ...   
28179              https://en.wikipedia.org/wiki/Boxty  28179            0   
28180              https://en.wikipedia.org/wiki/Boxty  28180            0   
28181              https://en.wikipedia.org/wiki/Boxty  28181            0   
28182              https://en.wikipedia.org/wiki/Boxty  28182            0   
28183              https://en.wikipedia.org/wiki/Boxty  28183            0   

         id_preproc  
0          EN_0_5_0  
1          EN_0_5_1  
2          EN_0_5_2  
3          EN_0_5_3  
4          EN_0_5_4  
...             ...  
28179   EN_6049_9_1  
28180   EN_6049_9_2  
28181   EN_6049_9_3  
28182   EN_6049_9_4  
28183  EN_6049_10_0  

[28184 rows x 8 columns]

In [49]:
ds_en = rem.map(lambda batch: translate_text(batch), batched=True)

trans_text_en = ds_en.to_pandas()['translated_text']

Map: 100%|██████████| 28184/28184 [7:07:02<00:00,  1.10 examples/s]  


In [50]:
trans_text_en

0        La familia se mudó a una plantación en Little ...
1        Cuando Augustine murió en 1743, Washington her...
2        Debido a la muerte de su padre, Washington no ...
3        Aprendió matemáticas y topografía de la tierra...
4        Al principio de la edad adulta, estaba escribi...
                               ...                        
28179    Brigid es la patrona de los lácteos y está aso...
28180                                   La tradición de St
28181    Brígida puede tener raíces en la historia paga...
28182    Boxty se sirve para el día de St Brigid con ot...
28183    Probablemente irlandés, posiblemente del arán ...
Name: translated_text, Length: 28184, dtype: object

In [53]:
rem_es = rem.to_pandas()
rem_es['text'] = trans_text_en

In [ ]:
rem_es['id_preproc'] = rem_es['id_preproc'].str.replace(r'^T_ES', 'T_EN', regex=True)


In [56]:
rem_es

title                                            summary  \
0      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
28179              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28180              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28181              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28182              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28183              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
0      La familia se mudó a una plantación en Little ...   en   
1      Cuando Augustine murió en 1743, Washington her...   en   
2      Debido a la muerte de su padre, Washington no ...   en   
3      Aprendió matemáticas y topografía de la tierra...   en   
4      Al principio de la edad adulta, estaba escribi...   en   
...                                                  ...  ...   
28179  Brigid es la patrona de los lácteos y está aso...   en   
28180                                 La tradición de St   en   
28181  Brígida puede tener raíces en la historia paga...   en   
28182  Boxty se sirve para el día de St Brigid con ot...   en   
28183  Probablemente irlandés, posiblemente del arán ...   en   

                                                   url  index  equivalence  \
0      https://en.wikipedia.org/wiki/George_Washington      0            1   
1      https://en.wikipedia.org/wiki/George_Washington      1            1   
2      https://en.wikipedia.org/wiki/George_Washington      2            1   
3      https://en.wikipedia.org/wiki/George_Washington      3            1   
4      https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                ...    ...          ...   
28179              https://en.wikipedia.org/wiki/Boxty  28179            0   
28180              https://en.wikipedia.org/wiki/Boxty  28180            0   
28181              https://en.wikipedia.org/wiki/Boxty  28181            0   
28182              https://en.wikipedia.org/wiki/Boxty  28182            0   
28183              https://en.wikipedia.org/wiki/Boxty  28183            0   

           id_preproc  
0          T_ES_0_5_0  
1          T_ES_0_5_1  
2          T_ES_0_5_2  
3          T_ES_0_5_3  
4          T_ES_0_5_4  
...               ...  
28179   T_ES_6049_9_1  
28180   T_ES_6049_9_2  
28181   T_ES_6049_9_3  
28182   T_ES_6049_9_4  
28183  T_ES_6049_10_0  

[28184 rows x 8 columns]

In [57]:
path_save = '/export/usuarios_ml4ds/ammesa/Data/1_segmented_data/micro_theme_match'
matched_es.to_parquet(os.path.join(path_save, 'es_2025_06_04_matched'))
matched_en.to_parquet(os.path.join(path_save, 'en_2025_06_04_matched'))
rem.to_parquet(os.path.join(path_save, 'remainder_english_files'))
rem_es.to_parquet(os.path.join(path_save, 'remainder_spanish_files'))

Creating parquet from Arrow format: 100%|██████████| 29/29 [00:00<00:00, 281.06ba/s]


In [62]:
matched_en = matched_en.drop(columns='matched_id_preproc_es')
matched_en

title  \
0           George Washington   
1           George Washington   
2           George Washington   
3           George Washington   
4           George Washington   
...                       ...   
12509  Bosnia and Herzegovina   
12511  Bosnia and Herzegovina   
12520  Bosnia and Herzegovina   
12522  Bosnia and Herzegovina   
12524  Bosnia and Herzegovina   

                                                 summary  \
0      George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington (February 22, 1732 [O.S. Feb...   
...                                                  ...   
12509  Bosnia and Herzegovina, sometimes known as Bos...   
12511  Bosnia and Herzegovina, sometimes known as Bos...   
12520  Bosnia and Herzegovina, sometimes known as Bos...   
12522  Bosnia and Herzegovina, sometimes known as Bos...   
12524  Bosnia and Herzegovina, sometimes known as Bos...   

                                                    text lang  \
0      George Washington (February 22, 1732 [O.S. Feb...   en   
1      Born in the Colony of Virginia, Washington bec...   en   
2      Washington was unanimously elected the first U...   en   
3      Washington's image is an icon of American cult...   en   
4      George Washington was born on February 22, 173...   en   
...                                                  ...  ...   
12509  Typical Bosnian songs are ganga, rera, and the...   en   
12511  Rural folk traditions in Bosnia and Herzegovin...   en   
12520  The Bosna Royal basketball club from Sarajevo ...   en   
12522  The Bosnian chess team was Champion of Yugosla...   en   
12524  Association football is the most popular sport...   en   

                                                     url     id  equivalence  \
0        https://en.wikipedia.org/wiki/George_Washington      0            1   
1        https://en.wikipedia.org/wiki/George_Washington      1            1   
2        https://en.wikipedia.org/wiki/George_Washington      2            1   
3        https://en.wikipedia.org/wiki/George_Washington      3            1   
4        https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                  ...    ...          ...   
12509  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12509            0   
12511  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12511            0   
12520  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12520            0   
12522  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12522            0   
12524  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12524            0   

        id_preproc  
0           EN_0_0  
1           EN_0_1  
2           EN_0_2  
3           EN_0_3  
4           EN_0_4  
...            ...  
12509  EN_6047_149  
12511  EN_6047_151  
12520  EN_6047_160  
12522  EN_6047_162  
12524  EN_6047_164  

[5068 rows x 8 columns]

In [63]:
rem.to_pandas()

title                                            summary  \
0      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
28179              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28180              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28181              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28182              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28183              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
0      The family moved to a plantation on Little Hun...   en   
1      When Augustine died in 1743, Washington inheri...   en   
2      Because of his father's death, Washington did ...   en   
3      He learned mathematics and land surveying, and...   en   
4      By early adulthood, he was writing with what h...   en   
...                                                  ...  ...   
28179  Brigid is the patron saint of dairy and she is...   en   
28180                                The tradition of St   en   
28181  Brigid may have roots in Ireland's pagan histo...   en   
28182  Boxty is served for St Brigid's Day with other...   en   
28183  Likely Irish, possibly from the Irish arán boc...   en   

                                                   url  index  equivalence  \
0      https://en.wikipedia.org/wiki/George_Washington      0            1   
1      https://en.wikipedia.org/wiki/George_Washington      1            1   
2      https://en.wikipedia.org/wiki/George_Washington      2            1   
3      https://en.wikipedia.org/wiki/George_Washington      3            1   
4      https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                ...    ...          ...   
28179              https://en.wikipedia.org/wiki/Boxty  28179            0   
28180              https://en.wikipedia.org/wiki/Boxty  28180            0   
28181              https://en.wikipedia.org/wiki/Boxty  28181            0   
28182              https://en.wikipedia.org/wiki/Boxty  28182            0   
28183              https://en.wikipedia.org/wiki/Boxty  28183            0   

         id_preproc  
0          EN_0_5_0  
1          EN_0_5_1  
2          EN_0_5_2  
3          EN_0_5_3  
4          EN_0_5_4  
...             ...  
28179   EN_6049_9_1  
28180   EN_6049_9_2  
28181   EN_6049_9_3  
28182   EN_6049_9_4  
28183  EN_6049_10_0  

[28184 rows x 8 columns]

# USING SAVED FILES

In [71]:
path_save = '/export/usuarios_ml4ds/ammesa/Data/1_segmented_data/micro_theme_match'
matched_es = pd.read_parquet(os.path.join(path_save, 'es_2025_06_04_matched'))
matched_en = pd.read_parquet(os.path.join(path_save, 'en_2025_06_04_matched'))
rem = pd.read_parquet(os.path.join(path_save, 'remainder_english_files'))
rem_es = pd.read_parquet(os.path.join(path_save, 'remainder_spanish_files'))

In [72]:
matched_en

title  \
0           George Washington   
1           George Washington   
2           George Washington   
3           George Washington   
4           George Washington   
...                       ...   
12509  Bosnia and Herzegovina   
12511  Bosnia and Herzegovina   
12520  Bosnia and Herzegovina   
12522  Bosnia and Herzegovina   
12524  Bosnia and Herzegovina   

                                                 summary  \
0      George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington (February 22, 1732 [O.S. Feb...   
...                                                  ...   
12509  Bosnia and Herzegovina, sometimes known as Bos...   
12511  Bosnia and Herzegovina, sometimes known as Bos...   
12520  Bosnia and Herzegovina, sometimes known as Bos...   
12522  Bosnia and Herzegovina, sometimes known as Bos...   
12524  Bosnia and Herzegovina, sometimes known as Bos...   

                                                    text lang  \
0      George Washington (February 22, 1732 [O.S. Feb...   en   
1      Born in the Colony of Virginia, Washington bec...   en   
2      Washington was unanimously elected the first U...   en   
3      Washington's image is an icon of American cult...   en   
4      George Washington was born on February 22, 173...   en   
...                                                  ...  ...   
12509  Typical Bosnian songs are ganga, rera, and the...   en   
12511  Rural folk traditions in Bosnia and Herzegovin...   en   
12520  The Bosna Royal basketball club from Sarajevo ...   en   
12522  The Bosnian chess team was Champion of Yugosla...   en   
12524  Association football is the most popular sport...   en   

                                                     url     id  equivalence  \
0        https://en.wikipedia.org/wiki/George_Washington      0            1   
1        https://en.wikipedia.org/wiki/George_Washington      1            1   
2        https://en.wikipedia.org/wiki/George_Washington      2            1   
3        https://en.wikipedia.org/wiki/George_Washington      3            1   
4        https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                  ...    ...          ...   
12509  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12509            0   
12511  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12511            0   
12520  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12520            0   
12522  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12522            0   
12524  https://en.wikipedia.org/wiki/Bosnia_and_Herze...  12524            0   

        id_preproc matched_id_preproc_es  
0           EN_0_0            ES_10000_0  
1           EN_0_1            ES_10048_1  
2           EN_0_2           ES_10086_45  
3           EN_0_3           ES_10000_77  
4           EN_0_4            ES_10000_7  
...            ...                   ...  
12509  EN_6047_149          ES_18013_124  
12511  EN_6047_151           ES_18044_11  
12520  EN_6047_160          ES_18013_131  
12522  EN_6047_162          ES_18013_127  
12524  EN_6047_164          ES_18013_126  

[5068 rows x 9 columns]

In [73]:
matched_es

title  \
12657     George Washington   
13996  Augustine Washington   
15067          Bill Clinton   
12734     George Washington   
12664     George Washington   
...                     ...   
16947             Eslovenia   
17637              Tragedia   
16954             Eslovenia   
16950             Eslovenia   
16949             Eslovenia   

                                                 summary  \
12657  George Washington (Westmoreland, Virginia, Amé...   
13996  Augustine Washington (Westmoreland, Virginia, ...   
15067  William Jefferson Clinton (nacido Blythe III;[...   
12734  George Washington (Westmoreland, Virginia, Amé...   
12664  George Washington (Westmoreland, Virginia, Amé...   
...                                                  ...   
16947  Eslovenia, cuyo nombre oficial es República de...   
17637  La tragedia es una forma literaria, teatral o ...   
16954  Eslovenia, cuyo nombre oficial es República de...   
16950  Eslovenia, cuyo nombre oficial es República de...   
16949  Eslovenia, cuyo nombre oficial es República de...   

                                                    text lang  \
12657  George Washington (Westmoreland, Virginia, Amé...   es   
13996  Agustín Washington nació en Westmoreland, Virg...   es   
15067  Algunos consideran que fue un presidente moder...   es   
12734  Junto con la familia biológica de Marta, como ...   es   
12664  George Washington nació el 22 de febrero de 17...   es   
...                                                  ...  ...   
16947  Entre los músicos populares contemporáneos est...   es   
17637  Estásimo: es la parte lírica-dramática donde e...   es   
16954  En balonmano, la selección masculina ha lograd...   es   
16950  El primer atleta esloveno en conseguir medalla...   es   
16949  Las disciplinas más populares en Eslovenia son...   es   

                                                     url     id  equivalence  \
12657    https://en.wikipedia.org/wiki/George_Washington  12657            1   
13996  https://en.wikipedia.org/wiki/Augustine_Washin...  13996            1   
15067         https://en.wikipedia.org/wiki/Bill_Clinton  15067            1   
12734    https://en.wikipedia.org/wiki/George_Washington  12734            1   
12664    https://en.wikipedia.org/wiki/George_Washington  12664            1   
...                                                  ...    ...          ...   
16947             https://en.wikipedia.org/wiki/Slovenia  16947            0   
17637              https://en.wikipedia.org/wiki/Tragedy  17637            0   
16954             https://en.wikipedia.org/wiki/Slovenia  16954            0   
16950             https://en.wikipedia.org/wiki/Slovenia  16950            0   
16949             https://en.wikipedia.org/wiki/Slovenia  16949            0   

           id_preproc matched_id_preproc_en  
12657    T_EN_10000_0                EN_0_0  
13996    T_EN_10048_1                EN_0_1  
15067   T_EN_10086_45                EN_0_2  
12734   T_EN_10000_77                EN_0_3  
12664    T_EN_10000_7                EN_0_4  
...               ...                   ...  
16947  T_EN_18013_124           EN_6047_149  
17637   T_EN_18044_11           EN_6047_151  
16954  T_EN_18013_131           EN_6047_160  
16950  T_EN_18013_127           EN_6047_162  
16949  T_EN_18013_126           EN_6047_164  

[5068 rows x 9 columns]

In [75]:
import re

def strip_msb_and_leading_zeros(s):
    match = re.match(r"T_EN_(\d+)_([0-9]+)", s)
    if not match:
        return s  # return original if not matching

    number, suffix = match.groups()

    # Remove the first non-zero digit (MSB)
    for i, ch in enumerate(number):
        if ch != '0':
            rest = number[i+1:]
            # Strip leading zeros from what's left
            rest = rest.lstrip('0')
            break
    else:
        rest = ''  # all zeros

    # If nothing remains, return single 0
    if not rest:
        rest = '0'

    return f"T_EN_{rest}_{suffix}"


In [76]:
matched_es['id_preproc'] = matched_es['id_preproc'].apply(strip_msb_and_leading_zeros)
matched_es

title  \
12657     George Washington   
13996  Augustine Washington   
15067          Bill Clinton   
12734     George Washington   
12664     George Washington   
...                     ...   
16947             Eslovenia   
17637              Tragedia   
16954             Eslovenia   
16950             Eslovenia   
16949             Eslovenia   

                                                 summary  \
12657  George Washington (Westmoreland, Virginia, Amé...   
13996  Augustine Washington (Westmoreland, Virginia, ...   
15067  William Jefferson Clinton (nacido Blythe III;[...   
12734  George Washington (Westmoreland, Virginia, Amé...   
12664  George Washington (Westmoreland, Virginia, Amé...   
...                                                  ...   
16947  Eslovenia, cuyo nombre oficial es República de...   
17637  La tragedia es una forma literaria, teatral o ...   
16954  Eslovenia, cuyo nombre oficial es República de...   
16950  Eslovenia, cuyo nombre oficial es República de...   
16949  Eslovenia, cuyo nombre oficial es República de...   

                                                    text lang  \
12657  George Washington (Westmoreland, Virginia, Amé...   es   
13996  Agustín Washington nació en Westmoreland, Virg...   es   
15067  Algunos consideran que fue un presidente moder...   es   
12734  Junto con la familia biológica de Marta, como ...   es   
12664  George Washington nació el 22 de febrero de 17...   es   
...                                                  ...  ...   
16947  Entre los músicos populares contemporáneos est...   es   
17637  Estásimo: es la parte lírica-dramática donde e...   es   
16954  En balonmano, la selección masculina ha lograd...   es   
16950  El primer atleta esloveno en conseguir medalla...   es   
16949  Las disciplinas más populares en Eslovenia son...   es   

                                                     url     id  equivalence  \
12657    https://en.wikipedia.org/wiki/George_Washington  12657            1   
13996  https://en.wikipedia.org/wiki/Augustine_Washin...  13996            1   
15067         https://en.wikipedia.org/wiki/Bill_Clinton  15067            1   
12734    https://en.wikipedia.org/wiki/George_Washington  12734            1   
12664    https://en.wikipedia.org/wiki/George_Washington  12664            1   
...                                                  ...    ...          ...   
16947             https://en.wikipedia.org/wiki/Slovenia  16947            0   
17637              https://en.wikipedia.org/wiki/Tragedy  17637            0   
16954             https://en.wikipedia.org/wiki/Slovenia  16954            0   
16950             https://en.wikipedia.org/wiki/Slovenia  16950            0   
16949             https://en.wikipedia.org/wiki/Slovenia  16949            0   

          id_preproc matched_id_preproc_en  
12657       T_EN_0_0                EN_0_0  
13996      T_EN_48_1                EN_0_1  
15067     T_EN_86_45                EN_0_2  
12734      T_EN_0_77                EN_0_3  
12664       T_EN_0_7                EN_0_4  
...              ...                   ...  
16947  T_EN_8013_124           EN_6047_149  
17637   T_EN_8044_11           EN_6047_151  
16954  T_EN_8013_131           EN_6047_160  
16950  T_EN_8013_127           EN_6047_162  
16949  T_EN_8013_126           EN_6047_164  

[5068 rows x 9 columns]

In [78]:
rem_es['id_preproc'] = rem_es['id_preproc'].str.replace(r'^T_ES', 'T_EN', regex=True)


In [79]:
rem_es

title                                            summary  \
0      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
28179              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28180              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28181              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28182              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28183              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
0      La familia se mudó a una plantación en Little ...   en   
1      Cuando Augustine murió en 1743, Washington her...   en   
2      Debido a la muerte de su padre, Washington no ...   en   
3      Aprendió matemáticas y topografía de la tierra...   en   
4      Al principio de la edad adulta, estaba escribi...   en   
...                                                  ...  ...   
28179  Brigid es la patrona de los lácteos y está aso...   en   
28180                                 La tradición de St   en   
28181  Brígida puede tener raíces en la historia paga...   en   
28182  Boxty se sirve para el día de St Brigid con ot...   en   
28183  Probablemente irlandés, posiblemente del arán ...   en   

                                                   url  index  equivalence  \
0      https://en.wikipedia.org/wiki/George_Washington      0            1   
1      https://en.wikipedia.org/wiki/George_Washington      1            1   
2      https://en.wikipedia.org/wiki/George_Washington      2            1   
3      https://en.wikipedia.org/wiki/George_Washington      3            1   
4      https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                ...    ...          ...   
28179              https://en.wikipedia.org/wiki/Boxty  28179            0   
28180              https://en.wikipedia.org/wiki/Boxty  28180            0   
28181              https://en.wikipedia.org/wiki/Boxty  28181            0   
28182              https://en.wikipedia.org/wiki/Boxty  28182            0   
28183              https://en.wikipedia.org/wiki/Boxty  28183            0   

           id_preproc  
0          T_EN_0_5_0  
1          T_EN_0_5_1  
2          T_EN_0_5_2  
3          T_EN_0_5_3  
4          T_EN_0_5_4  
...               ...  
28179   T_EN_6049_9_1  
28180   T_EN_6049_9_2  
28181   T_EN_6049_9_3  
28182   T_EN_6049_9_4  
28183  T_EN_6049_10_0  

[28184 rows x 8 columns]

In [80]:
rem

title                                            summary  \
0      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4      George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                  ...                                                ...   
28179              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28180              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28181              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28182              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   
28183              Boxty  Boxty (Irish: bacstaí or Irish: steaimpí) is a...   

                                                    text lang  \
0      The family moved to a plantation on Little Hun...   en   
1      When Augustine died in 1743, Washington inheri...   en   
2      Because of his father's death, Washington did ...   en   
3      He learned mathematics and land surveying, and...   en   
4      By early adulthood, he was writing with what h...   en   
...                                                  ...  ...   
28179  Brigid is the patron saint of dairy and she is...   en   
28180                                The tradition of St   en   
28181  Brigid may have roots in Ireland's pagan histo...   en   
28182  Boxty is served for St Brigid's Day with other...   en   
28183  Likely Irish, possibly from the Irish arán boc...   en   

                                                   url  index  equivalence  \
0      https://en.wikipedia.org/wiki/George_Washington      0            1   
1      https://en.wikipedia.org/wiki/George_Washington      1            1   
2      https://en.wikipedia.org/wiki/George_Washington      2            1   
3      https://en.wikipedia.org/wiki/George_Washington      3            1   
4      https://en.wikipedia.org/wiki/George_Washington      4            1   
...                                                ...    ...          ...   
28179              https://en.wikipedia.org/wiki/Boxty  28179            0   
28180              https://en.wikipedia.org/wiki/Boxty  28180            0   
28181              https://en.wikipedia.org/wiki/Boxty  28181            0   
28182              https://en.wikipedia.org/wiki/Boxty  28182            0   
28183              https://en.wikipedia.org/wiki/Boxty  28183            0   

         id_preproc  
0          EN_0_5_0  
1          EN_0_5_1  
2          EN_0_5_2  
3          EN_0_5_3  
4          EN_0_5_4  
...             ...  
28179   EN_6049_9_1  
28180   EN_6049_9_2  
28181   EN_6049_9_3  
28182   EN_6049_9_4  
28183  EN_6049_10_0  

[28184 rows x 8 columns]

In [81]:
rem["aux_id"] = rem["id_preproc"].str.rsplit("_", n=1).str[0]
grouped_en = (rem
                .groupby("aux_id")["text"]
                .agg(lambda x: ' '.join(x.astype(str).str.strip()))
                .reset_index()
                .rename(columns={"text": "assembled_text"}))

In [88]:
merged_en_df = (rem
                .merge(grouped_en, on="aux_id", how="outer")
                .drop(columns=['text', 'id_preproc'])
                .rename(columns={'aux_id': 'id_preproc', 
                                'assembled_text': 'text'})
                .drop_duplicates(subset=['id_preproc'])
                .assign(id_preproc=lambda x: 'T_' + x['id_preproc'])
                .assign(lang=lambda x: 'en')
                .reset_index(drop=True))


In [89]:
merged_en_df

title                                            summary  \
0       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                   ...                                                ...   
7584  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7585  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7586  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7587  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7588  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   

     lang                                                url  index  \
0      en    https://en.wikipedia.org/wiki/George_Washington      6   
1      en    https://en.wikipedia.org/wiki/George_Washington     11   
2      en    https://en.wikipedia.org/wiki/George_Washington     18   
3      en    https://en.wikipedia.org/wiki/George_Washington     22   
4      en    https://en.wikipedia.org/wiki/George_Washington     26   
...   ...                                                ...    ...   
7584   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1388   
7585   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1322   
7586   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1325   
7587   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1327   
7588   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1333   

      equivalence id_preproc  \
0               1  T_EN_0_10   
1               1  T_EN_0_12   
2               1  T_EN_0_14   
3               1  T_EN_0_16   
4               1  T_EN_0_18   
...           ...        ...   
7584            1  T_EN_9_45   
7585            1   T_EN_9_5   
7586            1   T_EN_9_6   
7587            1   T_EN_9_7   
7588            1   T_EN_9_8   

                                                   text  
0     Washington's party reached the Ohio River in N...  
1     The rest of the Virginia Regiment joined Washi...  
2     The Virginia Regiment was reconstituted in Aug...  
3     Under Washington, the Virginia Regiment had de...  
4     At Washington's urging, Governor Lord Botetour...  
...                                                 ...  
7584  William Polk Jesse student notebooks, 1919–192...  
7585  In 1907, Michelson had the honor of being the ...  
7586  He returned to military service in the closing...  
7587  Michelson died in Pasadena, California, at the...  
7588  Numerous awards, lectures, and honors have bee...  

[7589 rows x 8 columns]

In [99]:
rem_es["aux_id"] = rem_es["id_preproc"].str.rsplit("_", n=1).str[0]
grouped_es = (rem_es
                .groupby("aux_id")["text"]
                .agg(lambda x: ' '.join(x.astype(str).str.strip()))
                .reset_index()
                .rename(columns={"text": "assembled_text"}))

In [100]:
grouped_es

aux_id                                     assembled_text
0     T_EN_0_10  El partido de Washington llegó al río Ohio en ...
1     T_EN_0_12  El resto del Regimiento de Virginia se unió a ...
2     T_EN_0_14  El Regimiento de Virginia fue reconstituido en...
3     T_EN_0_16  Bajo Washington, el Regimiento de Virginia hab...
4     T_EN_0_18  A instancias de Washington, el Gobernador Lord...
...         ...                                                ...
7584  T_EN_9_45  William Polk Jesse cuadernos de estudiantes, 1...
7585   T_EN_9_5  En 1907, Michelson tuvo el honor de ser el pri...
7586   T_EN_9_6  Regresó al servicio militar en los últimos mes...
7587   T_EN_9_7  Michelson murió en Pasadena, California, a la ...
7588   T_EN_9_8  Numerosos premios, conferencias y honores se h...

[7589 rows x 2 columns]

In [101]:
merged_es_df = (rem_es
                .merge(grouped_es, on="aux_id", how="outer")
                .drop(columns=['text', 'id_preproc'])
                .rename(columns={'aux_id': 'id_preproc', 
                                'assembled_text': 'text'})
                .drop_duplicates(subset=['id_preproc'])
                .assign(id_preproc=lambda x: 'T_' + x['id_preproc'])
                .assign(lang=lambda x: 'en')
                .reset_index(drop=True))


In [102]:
merged_es_df['id_preproc'] = merged_es_df['id_preproc'].str.replace(r'^T_', '', regex=True)
merged_en_df['id_preproc'] = merged_en_df['id_preproc'].str.replace(r'^T_', '', regex=True)


In [105]:
merged_es_df['lang'] = 'es'
merged_es_df

title                                            summary  \
0       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                   ...                                                ...   
7584  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7585  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7586  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7587  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7588  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   

     lang                                                url  index  \
0      es    https://en.wikipedia.org/wiki/George_Washington      6   
1      es    https://en.wikipedia.org/wiki/George_Washington     11   
2      es    https://en.wikipedia.org/wiki/George_Washington     18   
3      es    https://en.wikipedia.org/wiki/George_Washington     22   
4      es    https://en.wikipedia.org/wiki/George_Washington     26   
...   ...                                                ...    ...   
7584   es  https://en.wikipedia.org/wiki/Albert_A._Michelson   1388   
7585   es  https://en.wikipedia.org/wiki/Albert_A._Michelson   1322   
7586   es  https://en.wikipedia.org/wiki/Albert_A._Michelson   1325   
7587   es  https://en.wikipedia.org/wiki/Albert_A._Michelson   1327   
7588   es  https://en.wikipedia.org/wiki/Albert_A._Michelson   1333   

      equivalence id_preproc  \
0               1  T_EN_0_10   
1               1  T_EN_0_12   
2               1  T_EN_0_14   
3               1  T_EN_0_16   
4               1  T_EN_0_18   
...           ...        ...   
7584            1  T_EN_9_45   
7585            1   T_EN_9_5   
7586            1   T_EN_9_6   
7587            1   T_EN_9_7   
7588            1   T_EN_9_8   

                                                   text  
0     El partido de Washington llegó al río Ohio en ...  
1     El resto del Regimiento de Virginia se unió a ...  
2     El Regimiento de Virginia fue reconstituido en...  
3     Bajo Washington, el Regimiento de Virginia hab...  
4     A instancias de Washington, el Gobernador Lord...  
...                                                 ...  
7584  William Polk Jesse cuadernos de estudiantes, 1...  
7585  En 1907, Michelson tuvo el honor de ser el pri...  
7586  Regresó al servicio militar en los últimos mes...  
7587  Michelson murió en Pasadena, California, a la ...  
7588  Numerosos premios, conferencias y honores se h...  

[7589 rows x 8 columns]

In [104]:
merged_en_df

title                                            summary  \
0       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
1       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
2       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
3       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
4       George Washington  George Washington (February 22, 1732 [O.S. Feb...   
...                   ...                                                ...   
7584  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7585  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7586  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7587  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   
7588  Albert A. Michelson  Albert Abraham Michelson (; December 19, 1852 ...   

     lang                                                url  index  \
0      en    https://en.wikipedia.org/wiki/George_Washington      6   
1      en    https://en.wikipedia.org/wiki/George_Washington     11   
2      en    https://en.wikipedia.org/wiki/George_Washington     18   
3      en    https://en.wikipedia.org/wiki/George_Washington     22   
4      en    https://en.wikipedia.org/wiki/George_Washington     26   
...   ...                                                ...    ...   
7584   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1388   
7585   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1322   
7586   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1325   
7587   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1327   
7588   en  https://en.wikipedia.org/wiki/Albert_A._Michelson   1333   

      equivalence id_preproc  \
0               1    EN_0_10   
1               1    EN_0_12   
2               1    EN_0_14   
3               1    EN_0_16   
4               1    EN_0_18   
...           ...        ...   
7584            1    EN_9_45   
7585            1     EN_9_5   
7586            1     EN_9_6   
7587            1     EN_9_7   
7588            1     EN_9_8   

                                                   text  
0     Washington's party reached the Ohio River in N...  
1     The rest of the Virginia Regiment joined Washi...  
2     The Virginia Regiment was reconstituted in Aug...  
3     Under Washington, the Virginia Regiment had de...  
4     At Washington's urging, Governor Lord Botetour...  
...                                                 ...  
7584  William Polk Jesse student notebooks, 1919–192...  
7585  In 1907, Michelson had the honor of being the ...  
7586  He returned to military service in the closing...  
7587  Michelson died in Pasadena, California, at the...  
7588  Numerous awards, lectures, and honors have bee...  

[7589 rows x 8 columns]

In [106]:

merged_es_df.to_parquet(os.path.join(path_save, 'es_2025_06_05_matched'))
merged_en_df.to_parquet(os.path.join(path_save, 'en_2025_06_05_matched'))